In [148]:
import os
import sys
import numpy as np
from collections import defaultdict
import gmpy2
import copy
import logging

inputfilepath = 'C:\EMOLGUI\A_O_C\Day17.txt'
#inputfilepath = 'C:\EMOLGUI\A_O_C\Day17.sample.txt'

In [149]:
rock1 = [['#', '#', '#', '#']]
rock1Model = np.array([[0, 0, 1, 1, 1, 1, 0]])

rock2 = [['.', '#', '.'], 
        ['#', '#', '#'],
        ['.', '#', '.']]
rock2Model = np.array([[0, 0, 0, 1, 0, 0, 0],
                [0, 0, 1, 1, 1, 0, 0],
                [0, 0, 0, 1, 0, 0, 0]])

rock3 = [['.', '.', '#'],
        ['.', '.', '#'],
        ['#', '#', '#']]
rock3Model = np.array([[0, 0, 1, 1, 1, 0, 0],
                [0, 0, 0, 0, 1, 0, 0],
                [0, 0, 0, 0, 1, 0, 0]]) # Model is reversed upside-down

rock4 = [['#'],
        ['#'],
        ['#'],
        ['#']]
rock4Model = np.array([[0, 0, 1, 0, 0, 0, 0],
                [0, 0, 1, 0, 0, 0, 0],
                [0, 0, 1, 0, 0, 0, 0],
                [0, 0, 1, 0, 0, 0, 0]])

rock5 = [['#', '#'],
        ['#', '#']]
rock5Model = np.array([[0, 0, 1, 1, 0, 0, 0],
                [0, 0, 1, 1, 0, 0, 0]])

rockSeq = [rock1Model, rock2Model, rock3Model, rock4Model, rock5Model]

cave = np.array([[1, 1, 1, 1, 1, 1, 1]])

with open(inputfilepath,'r') as f:
    jetsSeq = list(f.readline().rstrip())

In [150]:
len(jetsSeq), jetsSeq

(10091,
 ['>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '<',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '<',
  '>',
  '>',
  '>',
  '<',
  '>',
  '>',
  '>',
  '<',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '>',
  '>',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '<',
  '<',
  '>',
  '>',
  '>',
  '<',
  '<',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '<',
  '>',
  '>',
  '<',
  '<',
  '>',
  '>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '<',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '<',
  '<',
  '<',
  '>',
  '>',
  '>',
  '>',
  '<',
  '>',
  '<',
  '>'

In [151]:
for rock in rockSeq:
    print(rock.shape)

(1, 7)
(3, 7)
(3, 7)
(4, 7)
(2, 7)


In [152]:
cave.shape[0]

1

In [153]:
def testCaveRock(rock, height, cave):

    overlap_level = cave.shape[0] - height
    overlap_height = min(rock.shape[0], overlap_level)
    if overlap_level < 1:
        return True
    return np.max(cave[height:height + overlap_height,:] + rock[0:overlap_height,:]) == 1

In [154]:
def lateralMove(rock, height, move, cave):

    if move == '>':
        if max(rock[:,-1] == 1):
            return rock
        rock = rock[:,[6, 0, 1, 2, 3, 4, 5]]
    elif move == '<':
        if max(rock[:,0] == 1):
            return rock
        rock = rock[:,[1, 2, 3, 4, 5, 6, 0]]
    
    if testCaveRock(rock,height,cave):
        return rock

    # Lateral movement is not valid, undoing it
    if move == '<':
        rock = rock[:,[6, 0, 1, 2, 3, 4, 5]]
    elif move == '>':
        rock = rock[:,[1, 2, 3, 4, 5, 6, 0]]
    return rock
    


In [155]:
def fallMove(rock, height, cave):
    fallHeight = height - 1

    if testCaveRock(rock, fallHeight, cave):
        return cave, fallHeight

    # Fall movement is not valid, undoing fall and fixating rock on cave
    fallHeight = height

    overlap_level = cave.shape[0] - height
    overlap_height = min(rock.shape[0], overlap_level)

    cave[fallHeight: fallHeight + overlap_height,:] = cave[fallHeight: fallHeight + overlap_height,:] + rock[0:overlap_height,:]

    if rock.shape[0] > overlap_height:
        for addedLayer in range(overlap_height,rock.shape[0]):
            cave = np.append(cave, [rock[addedLayer,:]], axis = 0)
    
    #print(cave)
    
    return cave, fallHeight


In [110]:
rockIndex = 0
movCount = 0
currentRock = copy.copy(rockSeq[rockIndex])
cave = np.array([[1, 1, 1, 1, 1, 1, 1]])
rockHeight = cave.shape[0] + 3
while rockIndex < 2022:
    nextMove = jetsSeq[movCount % len(jetsSeq)]
    print(f'Next move {movCount}, starting height {rockHeight}, move is {nextMove}')
    print('    Before lateral movement: ')
    print(currentRock)
    currentRock = lateralMove(currentRock,rockHeight,nextMove,cave)
    print('    After lateral movement: ')
    print(currentRock)
    prevHeight = rockHeight
    cave, rockHeight = fallMove(currentRock,rockHeight,cave)
    movCount += 1
    
    print('    Final cave state: ')
    print(cave)

    if prevHeight == rockHeight:
        rockIndex += 1
        print(f'Rock is fixated: getting next rock {rockIndex}')
        rockIndex = rockIndex
        rockHeight = cave.shape[0] + 3
        currentRock = copy.copy(rockSeq[rockIndex % len(rockSeq)])

    if movCount == 50:
        rockIndex

print(f'The cave is {cave.shape[0] - 1} units tall')



Next move 0, starting height 4, move is >
    Before lateral movement: 
[[0 0 1 1 1 1 0]]
    After lateral movement: 
[[0 0 0 1 1 1 1]]
    Final cave state: 
[[1 1 1 1 1 1 1]]
Next move 1, starting height 3, move is <
    Before lateral movement: 
[[0 0 0 1 1 1 1]]
    After lateral movement: 
[[0 0 1 1 1 1 0]]
    Final cave state: 
[[1 1 1 1 1 1 1]]
Next move 2, starting height 2, move is <
    Before lateral movement: 
[[0 0 1 1 1 1 0]]
    After lateral movement: 
[[0 1 1 1 1 0 0]]
    Final cave state: 
[[1 1 1 1 1 1 1]]
Next move 3, starting height 1, move is <
    Before lateral movement: 
[[0 1 1 1 1 0 0]]
    After lateral movement: 
[[1 1 1 1 0 0 0]]
    Final cave state: 
[[1 1 1 1 1 1 1]
 [1 1 1 1 0 0 0]]
Rock is fixated: getting next rock 1
Next move 4, starting height 5, move is <
    Before lateral movement: 
[[0 0 0 1 0 0 0]
 [0 0 1 1 1 0 0]
 [0 0 0 1 0 0 0]]
    After lateral movement: 
[[0 0 1 0 0 0 0]
 [0 1 1 1 0 0 0]
 [0 0 1 0 0 0 0]]
    Final cave state: 
[[1 1 

In [118]:
np.max(np.where(np.sum(cave, axis=1)==7))


2856

In [120]:
caveCop = copy.copy(cave)
caveCop[2856:,:]

array([[1, 1, 1, ..., 1, 1, 1],
       [0, 1, 0, ..., 1, 1, 1],
       [1, 1, 1, ..., 1, 1, 1],
       ...,
       [0, 1, 0, ..., 1, 0, 0],
       [0, 0, 0, ..., 1, 0, 0],
       [0, 0, 0, ..., 1, 0, 0]])

#### QUESTION 2

In [157]:
# Locating a repeating cycle in the falling rocks

# First generate a pretty long list of partial results (rocks height growth after each new rock settles, for the first 100 000 rocks). Then look for a repeating pattern (a long one) in that sequence.

rockIndex = 0
movCount = 0
removedRows = 0
heightsGrowthList = []
caveHeight = 1
currentRock = copy.copy(rockSeq[rockIndex])
cave = np.array([[1, 1, 1, 1, 1, 1, 1]])
rockHeight = cave.shape[0] + 3
while rockIndex < 100_000:
    nextMove = jetsSeq[movCount % len(jetsSeq)]
    #print(f'Next move {movCount}, starting height {rockHeight}, move is {nextMove}')
    #print('    Before lateral movement: ')
    #print(currentRock)
    currentRock = lateralMove(currentRock,rockHeight,nextMove,cave)
    #print('    After lateral movement: ')
    #print(currentRock)
    prevHeight = rockHeight
    cave, rockHeight = fallMove(currentRock,rockHeight,cave)
    movCount += 1
    
    #print('    Final cave state: ')
    #print(cave)

    if prevHeight == rockHeight:
        newCaveHeight = cave.shape[0]
        heightsGrowthList.append(newCaveHeight - caveHeight)

        if np.max(np.where(np.sum(cave, axis=1)==7)) > 1:
            removedRows += np.max(np.where(np.sum(cave, axis=1)==7))
            cave = cave[np.max(np.where(np.sum(cave, axis=1)==7)):,:]

        caveHeight = cave.shape[0]
        rockIndex += 1
        #print(f'Rock is fixated: getting next rock {rockIndex}')
        rockIndex = rockIndex
        rockHeight = cave.shape[0] + 3
        currentRock = copy.copy(rockSeq[rockIndex % len(rockSeq)])



print(f'The cave is {removedRows + cave.shape[0] - 1} units tall')



The cave is 156558 units tall


In [146]:
heightsGrowthList

[1,
 3,
 2,
 1,
 2,
 1,
 3,
 2,
 2,
 0,
 1,
 3,
 2,
 0,
 2,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 3,
 2,
 0,
 0,
 1,
 3,
 3,
 4,
 0,
 1,
 2,
 3,
 0,
 1,
 1,
 3,
 2,
 2,
 0,
 0,
 2,
 3,
 4,
 0,
 1,
 2,
 1,
 2,
 0,


In [162]:
# Long for a repeating pattern (of length multiple of 5) within the previously generated list of values. We scan every possibility from 5 till 5000.
for cycle in range(5,5000,5):
    cycleTest = [sum(heightsGrowthList[i:i+cycle]) for i in range(1,5000)]
    if max(cycleTest[-1000:]) == min(cycleTest[-1000:]):
        print(f'cycle tested {cycle}')
        print([sum(heightsGrowthList[i:i+cycle]) for i in range(1,5000)])

cycle tested 1740
[2717, 2717, 2716, 2714, 2714, 2714, 2713, 2713, 2717, 2717, 2716, 2716, 2715, 2713, 2713, 2714, 2717, 2714, 2716, 2714, 2714, 2714, 2714, 2714, 2714, 2715, 2716, 2716, 2720, 2720, 2720, 2721, 2722, 2721, 2723, 2724, 2724, 2727, 2723, 2725, 2726, 2727, 2728, 2726, 2726, 2726, 2726, 2729, 2728, 2728, 2728, 2725, 2723, 2723, 2723, 2723, 2723, 2723, 2719, 2719, 2719, 2719, 2720, 2718, 2716, 2715, 2714, 2713, 2714, 2714, 2713, 2713, 2710, 2713, 2715, 2715, 2715, 2712, 2714, 2712, 2713, 2713, 2716, 2719, 2719, 2719, 2719, 2720, 2718, 2718, 2718, 2718, 2717, 2713, 2713, 2712, 2711, 2709, 2711, 2713, 2713, 2713, 2713, 2712, 2711, 2710, 2709, 2709, 2709, 2707, 2707, 2708, 2707, 2705, 2707, 2707, 2707, 2709, 2711, 2711, 2712, 2712, 2712, 2714, 2716, 2716, 2716, 2718, 2717, 2717, 2717, 2714, 2714, 2716, 2716, 2716, 2715, 2714, 2716, 2716, 2715, 2713, 2713, 2713, 2713, 2713, 2713, 2713, 2713, 2715, 2715, 2716, 2714, 2716, 2716, 2716, 2716, 2716, 2714, 2712, 2713, 2713, 2714, 271

In [178]:
# Cycle found of length 1740, sumValue 2724, starts at position 175
cycleTest = [sum(heightsGrowthList[i:i+1740]) for i in range(0,5000)]
cycleTest[174:178]

[2722, 2724, 2724, 2724]

In [181]:
# First 175 positions (not cycle) amount to 264 height
sum(heightsGrowthList[0:175]), sum(heightsGrowthList[175:175+1740])

(264, 2724)

In [183]:
# Number of full cycles included: 574712643
int((1_000_000_000_000 - 175)/1740)

574712643

In [185]:
total_length = 574712643*1740 + 175
1_000_000_000_000 - total_length

1005

In [187]:
# Trailing rocks at the end: 1005 (in a cycle):
trailHeight = sum(heightsGrowthList[175:175+1005])
trailHeight

1586

In [189]:
TotalCumulatedHeight = 264 + 574712643*2724 + trailHeight
TotalCumulatedHeight

1565517241382

In [ ]:
1565517241382